In [7]:
%pip install numpy
%pip install Pillow
%pip install opencv-python

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
  Using cached opencv_python-4.11.0.86-cp37-abi3-macosx_13_0_arm64.whl.metadata (20 kB)
Using cached opencv_python-4.11.0.86-cp37-abi3-macosx_13_0_arm64.whl (37.3 MB)
Note: you may need to restart the kernel to use updated packages.


In [36]:
import random
import numpy as np
from PIL import Image, ImageEnhance
import cv2
import hashlib

def get_video_rng(video_identifier: str) -> random.Random:
    """
    Create a deterministic RNG from the video_identifier string.
    Same identifier → same seed → same random sequence.
    Different identifiers → different seeds.
    """
    # Use MD5 (or SHA256) of the identifier, mod 2**32 for a 32-bit seed
    digest = hashlib.md5(video_identifier.encode("utf-8")).hexdigest()
    seed   = int(digest, 16) % (2**32)
    return random.Random(seed)

def random_crop_and_resize(
    img: np.ndarray,
    output_size: tuple[int, int],
    left,
    top,
    crop_w,
    crop_h,
    scale_range: tuple[float, float] = (0.5, 1.0),
    interpolation: int = Image.BILINEAR,
    rng: random.Random | None = None,
) -> np.ndarray:
    """
    Randomly crop+resize using the provided RNG (or Python's global if None).
    """
    if rng is None:
        rng = random
    
    pil = Image.fromarray(img)    
    patch   = pil.crop((left, top, left + crop_w, top + crop_h))
    resized = patch.resize(output_size, interpolation)
    return np.array(resized)


def color_jitter_manual(
    img: np.ndarray,
    brightness: float = 0.4,
    contrast:   float = 0.4,
    saturation: float = 0.4,
    rng: random.Random | None = None,
) -> np.ndarray:
    """
    Apply deterministic (w.r.t. rng) brightness/contrast/saturation jitter.
    """
    if rng is None:
        rng = random
    
    pil = Image.fromarray(img)
    
    # brightness
    factor = 1 + brightness
    pil = ImageEnhance.Brightness(pil).enhance(factor)
    
    # contrast
    factor = 1 + contrast
    pil = ImageEnhance.Contrast(pil).enhance(factor)
    
    # saturation
    factor = 1 + saturation
    pil = ImageEnhance.Color(pil).enhance(factor)
    
    return np.array(pil)


def crop_color_jitter(
    img: np.ndarray,
    left,
    top,
    crop_w,
    crop_h,
    brightness,
    contrast,
    saturation,
    crop_size: tuple[int, int] = (224, 224),
    rng: random.Random | None = None,
) -> np.ndarray:
    """
    Combines random_crop_and_resize + color_jitter_manual, all driven by the same RNG.
    """
    patch = random_crop_and_resize(img, crop_size,left, top, crop_w, crop_h, rng=rng)
    return color_jitter_manual(patch, brightness=brightness, contrast=contrast, saturation=saturation, rng=rng)


def sobel_filter(img: np.ndarray) -> np.ndarray:
    """
    Grayscale→Sobel edge map, returned as a 3-channel uint8 array.
    (No RNG needed here.)
    """
    gray   = cv2.cvtColor(img, cv2.COLOR_RGB2GRAY)
    sobelx = cv2.Sobel(gray, cv2.CV_64F, 1, 0, ksize=3)
    sobely = cv2.Sobel(gray, cv2.CV_64F, 0, 1, ksize=3)
    mag    = np.hypot(sobelx, sobely)
    if mag.max() > 0:
        mag = mag / mag.max()
    sobel_uint8 = (mag * 255).astype(np.uint8)
    return cv2.cvtColor(sobel_uint8, cv2.COLOR_GRAY2RGB)


def crop_sobel(
    img: np.ndarray,
    left,
    top,
    crop_w,
    crop_h,
    crop_size: tuple[int, int] = (224, 224),
    rng: random.Random | None = None,
) -> np.ndarray:
    """
    Random crop+resize followed by Sobel. RNG only for the crop.
    """
    patch = random_crop_and_resize(img, crop_size, left,
    top,
    crop_w,
    crop_h, rng=rng)
    return sobel_filter(patch)

Perform the augmentations

In [38]:
from moviepy import VideoFileClip
import os

os.mkdir("augmented_data/crop_color")
os.mkdir("augmented_data/crop_sobel")
for instrument in os.listdir("clipped_data"):
    if instrument != ".DS_Store":
        os.mkdir("augmented_data/crop_color/" + instrument)
        os.mkdir("augmented_data/crop_sobel/" + instrument)
        for file_name in os.listdir("clipped_data/"+instrument):
            if file_name[-1] == "3":
                continue
            
            clip = VideoFileClip("clipped_data/"+instrument+"/"+file_name)
            rng = get_video_rng(file_name)  # same seed every run for this file
            
            img = clip.get_frame(0)
            pil = Image.fromarray(img)
            orig_w, orig_h = pil.size
            
            # pick scale
            scale = rng.uniform(0.5, 1)
            crop_w = min(int(scale * orig_w), orig_w)
            crop_h = min(int(scale * orig_h), orig_h)
            
            # pick crop corner
            left = rng.randint(0, orig_w - crop_w)
            top  = rng.randint(0, orig_h - crop_h)
            
            brightness = rng.uniform(-0.4, 0.4)
            contrast = rng.uniform(-0.4, 0.4)
            saturation = rng.uniform(-0.4, 0.4)
            
            crop_color = clip.transform(lambda get_frame,t : crop_color_jitter(get_frame(t), left, top, crop_w, crop_h, brightness, contrast, saturation, rng=rng), keep_duration=True)  
            crop_color.write_videofile("augmented_data/crop_color/" + instrument + "/" + file_name, audio=False)
            clip = VideoFileClip("clipped_data/"+instrument+"/"+file_name)
            crop_sobel_clip = clip.transform(lambda get_frame,t : crop_sobel(get_frame(t), left, top, crop_w, crop_h, rng=rng), keep_duration=True)
            crop_sobel_clip.write_videofile("augmented_data/crop_sobel/" + instrument + "/" + file_name, audio=False)

{'video_found': True, 'audio_found': True, 'metadata': {'major_brand': 'isom', 'minor_version': '512', 'compatible_brands': 'isomiso2avc1mp41', 'encoder': 'Lavf61.7.100'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'video', 'language': None, 'default': True, 'size': [640, 360], 'bitrate': 819, 'fps': 29.97002997002997, 'codec_name': 'h264', 'profile': '(High)', 'metadata': {'Metadata': '', 'handler_name': 'VideoHandler', 'vendor_id': '[0][0][0][0]', 'encoder': 'Lavc61.19.100 libx264'}}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': True, 'fps': 44100, 'bitrate': 126, 'metadata': {'Metadata': '', 'handler_name': 'SoundHandler', 'vendor_id': '[0][0][0][0]'}}], 'input_number': 0}], 'duration': 5.0, 'bitrate': 953, 'start': 0.0, 'default_video_input_number': 0, 'default_video_stream_number': 0, 'video_codec_name': 'h264', 'video_profile': '(High)', 'video_size': [640, 360], 'video_bitrate': 819, 'video_fps':

MoviePy - Done !
MoviePy - video ready augmented_data/crop_color/congas/Kachiro Thompson Conga Solo Fibercraft Series MEINL Percussion.mp4
{'video_found': True, 'audio_found': True, 'metadata': {'major_brand': 'isom', 'minor_version': '512', 'compatible_brands': 'isomiso2avc1mp41', 'encoder': 'Lavf61.7.100'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'video', 'language': None, 'default': True, 'size': [640, 360], 'bitrate': 819, 'fps': 29.97002997002997, 'codec_name': 'h264', 'profile': '(High)', 'metadata': {'Metadata': '', 'handler_name': 'VideoHandler', 'vendor_id': '[0][0][0][0]', 'encoder': 'Lavc61.19.100 libx264'}}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': True, 'fps': 44100, 'bitrate': 126, 'metadata': {'Metadata': '', 'handler_name': 'SoundHandler', 'vendor_id': '[0][0][0][0]'}}], 'input_number': 0}], 'duration': 5.0, 'bitrate': 953, 'start': 0.0, 'default_video_input_number': 0, 'default_v

MoviePy - Done !
MoviePy - video ready augmented_data/crop_sobel/congas/Kachiro Thompson Conga Solo Fibercraft Series MEINL Percussion.mp4
{'video_found': True, 'audio_found': True, 'metadata': {'major_brand': 'isom', 'minor_version': '512', 'compatible_brands': 'isomiso2avc1mp41', 'encoder': 'Lavf61.7.100'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'video', 'language': None, 'default': True, 'size': [640, 360], 'bitrate': 250, 'fps': 23.976023976023978, 'codec_name': 'h264', 'profile': '(High)', 'metadata': {'Metadata': '', 'handler_name': 'VideoHandler', 'vendor_id': '[0][0][0][0]', 'encoder': 'Lavc61.19.100 libx264'}}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': True, 'fps': 44100, 'bitrate': 127, 'metadata': {'Metadata': '', 'handler_name': 'SoundHandler', 'vendor_id': '[0][0][0][0]'}}], 'input_number': 0}], 'duration': 5.0, 'bitrate': 385, 'start': 0.0, 'default_video_input_number': 0, 'default_

MoviePy - Done !
MoviePy - video ready augmented_data/crop_color/congas/Oh When The Saints- Conga Solo.mp4
{'video_found': True, 'audio_found': True, 'metadata': {'major_brand': 'isom', 'minor_version': '512', 'compatible_brands': 'isomiso2avc1mp41', 'encoder': 'Lavf61.7.100'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'video', 'language': None, 'default': True, 'size': [640, 360], 'bitrate': 250, 'fps': 23.976023976023978, 'codec_name': 'h264', 'profile': '(High)', 'metadata': {'Metadata': '', 'handler_name': 'VideoHandler', 'vendor_id': '[0][0][0][0]', 'encoder': 'Lavc61.19.100 libx264'}}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': True, 'fps': 44100, 'bitrate': 127, 'metadata': {'Metadata': '', 'handler_name': 'SoundHandler', 'vendor_id': '[0][0][0][0]'}}], 'input_number': 0}], 'duration': 5.0, 'bitrate': 385, 'start': 0.0, 'default_video_input_number': 0, 'default_video_stream_number': 0, 'video_

MoviePy - Done !
MoviePy - video ready augmented_data/crop_sobel/congas/Oh When The Saints- Conga Solo.mp4
{'video_found': True, 'audio_found': True, 'metadata': {'major_brand': 'isom', 'minor_version': '512', 'compatible_brands': 'isomiso2avc1mp41', 'encoder': 'Lavf61.7.100'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'video', 'language': None, 'default': True, 'size': [490, 360], 'bitrate': 457, 'fps': 29.97002997002997, 'codec_name': 'h264', 'profile': '(High)', 'metadata': {'Metadata': '', 'handler_name': 'VideoHandler', 'vendor_id': '[0][0][0][0]', 'encoder': 'Lavc61.19.100 libx264'}}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': True, 'fps': 44100, 'bitrate': 127, 'metadata': {'Metadata': '', 'handler_name': 'SoundHandler', 'vendor_id': '[0][0][0][0]'}}], 'input_number': 0}], 'duration': 5.0, 'bitrate': 593, 'start': 0.0, 'default_video_input_number': 0, 'default_video_stream_number': 0, 'video_c

...

MoviePy - Done !
MoviePy - video ready augmented_data/crop_sobel/flute/Claude Debussy - Syrinx (La Flute de Pan for flute solo).mp4
{'video_found': True, 'audio_found': True, 'metadata': {'major_brand': 'isom', 'minor_version': '512', 'compatible_brands': 'isomiso2avc1mp41', 'encoder': 'Lavf61.7.100'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'video', 'language': None, 'default': True, 'size': [480, 360], 'bitrate': 311, 'fps': 29.97002997002997, 'codec_name': 'h264', 'profile': '(High)', 'metadata': {'Metadata': '', 'handler_name': 'VideoHandler', 'vendor_id': '[0][0][0][0]', 'encoder': 'Lavc61.19.100 libx264'}}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': True, 'fps': 44100, 'bitrate': 128, 'metadata': {'Metadata': '', 'handler_name': 'SoundHandler', 'vendor_id': '[0][0][0][0]'}}], 'input_number': 0}], 'duration': 5.0, 'bitrate': 449, 'start': 0.0, 'default_video_input_number': 0, 'default_video_st

MoviePy - Done !
MoviePy - video ready augmented_data/crop_color/flute/Searching for Friends (Final Fantasy 6), flute solo cover.mp4
{'video_found': True, 'audio_found': True, 'metadata': {'major_brand': 'isom', 'minor_version': '512', 'compatible_brands': 'isomiso2avc1mp41', 'encoder': 'Lavf61.7.100'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'video', 'language': None, 'default': True, 'size': [480, 360], 'bitrate': 311, 'fps': 29.97002997002997, 'codec_name': 'h264', 'profile': '(High)', 'metadata': {'Metadata': '', 'handler_name': 'VideoHandler', 'vendor_id': '[0][0][0][0]', 'encoder': 'Lavc61.19.100 libx264'}}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': True, 'fps': 44100, 'bitrate': 128, 'metadata': {'Metadata': '', 'handler_name': 'SoundHandler', 'vendor_id': '[0][0][0][0]'}}], 'input_number': 0}], 'duration': 5.0, 'bitrate': 449, 'start': 0.0, 'default_video_input_number': 0, 'default_video_s

MoviePy - Done !
MoviePy - video ready augmented_data/crop_sobel/flute/Searching for Friends (Final Fantasy 6), flute solo cover.mp4
{'video_found': True, 'audio_found': True, 'metadata': {'major_brand': 'isom', 'minor_version': '512', 'compatible_brands': 'isomiso2avc1mp41', 'encoder': 'Lavf61.7.100'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'video', 'language': None, 'default': True, 'size': [640, 360], 'bitrate': 430, 'fps': 30.0, 'codec_name': 'h264', 'profile': '(High)', 'metadata': {'Metadata': '', 'handler_name': 'VideoHandler', 'vendor_id': '[0][0][0][0]', 'encoder': 'Lavc61.19.100 libx264'}}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': True, 'fps': 44100, 'bitrate': 127, 'metadata': {'Metadata': '', 'handler_name': 'SoundHandler', 'vendor_id': '[0][0][0][0]'}}], 'input_number': 0}], 'duration': 5.0, 'bitrate': 570, 'start': 0.0, 'default_video_input_number': 0, 'default_video_stream_number'

MoviePy - Done !
MoviePy - video ready augmented_data/crop_color/flute/Victor's Piano Solo - Corpse bride (Flute cover).mp4
{'video_found': True, 'audio_found': True, 'metadata': {'major_brand': 'isom', 'minor_version': '512', 'compatible_brands': 'isomiso2avc1mp41', 'encoder': 'Lavf61.7.100'}, 'inputs': [{'streams': [{'input_number': 0, 'stream_number': 0, 'stream_type': 'video', 'language': None, 'default': True, 'size': [640, 360], 'bitrate': 430, 'fps': 30.0, 'codec_name': 'h264', 'profile': '(High)', 'metadata': {'Metadata': '', 'handler_name': 'VideoHandler', 'vendor_id': '[0][0][0][0]', 'encoder': 'Lavc61.19.100 libx264'}}, {'input_number': 0, 'stream_number': 1, 'stream_type': 'audio', 'language': None, 'default': True, 'fps': 44100, 'bitrate': 127, 'metadata': {'Metadata': '', 'handler_name': 'SoundHandler', 'vendor_id': '[0][0][0][0]'}}], 'input_number': 0}], 'duration': 5.0, 'bitrate': 570, 'start': 0.0, 'default_video_input_number': 0, 'default_video_stream_number': 0, 'vid

MoviePy - Done !
MoviePy - video ready augmented_data/crop_sobel/flute/Victor's Piano Solo - Corpse bride (Flute cover).mp4
